<a href="https://www.kaggle.com/code/dalepeh/citibike-2211-geospatial-visualization?scriptVersionId=115263874" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

## 1. Import Libraries

In [1]:
import pandas as pd
import numpy as np
import folium

## 2. Import Data

In [2]:
citibike=pd.read_csv('/kaggle/input/202211-citibike-tripdata/202211-citibike-tripdata.csv')

/opt/conda/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3552: DtypeWarning: Columns (5,7) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [3]:
citibike.head(5)

ride_id rideable_type           started_at             ended_at  \
0  211A73DFC6752EFC  classic_bike  2022-11-30 21:36:23  2022-11-30 21:49:31   
1  568E7F54B3EFB8C3  classic_bike  2022-11-20 11:06:30  2022-11-20 11:17:18   
2  0ED37DE3609F47A1  classic_bike  2022-11-17 09:48:34  2022-11-17 09:56:14   
3  AF0F9BAB2B4AA126  classic_bike  2022-11-02 12:23:36  2022-11-02 12:26:35   
4  215FF85772BA2D2B  classic_bike  2022-11-07 16:46:20  2022-11-07 16:54:16   

           start_station_name start_station_id  \
0             2 Ave & E 29 St          6122.09   
1       E 97 St & Madison Ave          7393.09   
2       E 97 St & Madison Ave          7393.09   
3  Morningside Ave & W 123 St          7741.01   
4             2 Ave & E 29 St          6122.09   

                      end_station_name end_station_id  start_lat  start_lng  \
0                 Pitt St & Stanton St        5406.04  40.741724 -73.978093   
1                      E 74 St & 1 Ave        6953.08  40.787826 -73.953423   
2  Adam Clayton Powell Blvd & W 118 St        7670.09  40.787899 -73.953396   
3  Adam Clayton Powell Blvd & W 118 St        7670.09  40.809931 -73.955209   
4                      W 13 St & 5 Ave        5947.04  40.741803 -73.978004   

     end_lat    end_lng member_casual  
0  40.719261 -73.981780        member  
1  40.768974 -73.954823        member  
2  40.804372 -73.951475        member  
3  40.804372 -73.951475        member  
4  40.735445 -73.994310        member

In [4]:
citibike.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2460105 entries, 0 to 2460104
Data columns (total 13 columns):
 #   Column              Dtype  
---  ------              -----  
 0   ride_id             object 
 1   rideable_type       object 
 2   started_at          object 
 3   ended_at            object 
 4   start_station_name  object 
 5   start_station_id    object 
 6   end_station_name    object 
 7   end_station_id      object 
 8   start_lat           float64
 9   start_lng           float64
 10  end_lat             float64
 11  end_lng             float64
 12  member_casual       object 
dtypes: float64(4), object(9)
memory usage: 244.0+ MB


## 3. Clearning and check for null values and duplicates

In [5]:
#check for missing data

citibike.isnull().values.any()

True

In [6]:
# drop all the NaN entries
citibike=citibike.dropna()

In [7]:
#Check the top usage count
citibike['start_station_name'].value_counts()[:20]

Broadway & W 58 St                   11610
W 21 St & 6 Ave                      11219
West St & Chambers St                 8691
1 Ave & E 68 St                       8624
W 31 St & 7 Ave                       8610
University Pl & E 14 St               8221
Columbus Ave & W 72 St                7865
6 Ave & W 33 St                       7769
8 Ave & W 33 St                       7727
8 Ave & W 16 St                       7711
11 Ave & W 41 St                      7687
E 40 St & Park Ave                    7680
Broadway & E 21 St                    7612
E 33 St & 1 Ave                       7520
E 17 St & Broadway                    7434
Cleveland Pl & Spring St              7427
Grand Army Plaza & Central Park S     7351
W 41 St & 8 Ave                       7328
Broadway & W 25 St                    7125
9 Ave & W 22 St                       6854
Name: start_station_name, dtype: int64

In [8]:
#Check the least usage count
citibike['start_station_name'].value_counts()[-20:]

W 52 St & 11 Ave                 30
Decatur Ave & Oliver Pl          30
Bergen St & Troy Ave             28
64 St & 3 Ave                    26
Bailey Ave & W 193 St            26
9 Ave & W 204 St                 25
St Marks Ave & Rochester Ave     25
Park Pl & Utica Ave              24
2 Av & 37 St                     22
Decatur Ave & E 197 St           21
Macon St & Howard Ave            21
Macon St & Lewis Ave             17
65 St & 2 Ave                    14
Pacific St & Rochester Ave       13
Eastern Pkwy & Rochester Ave     12
Sterling Pl & Schenectady Ave     6
Bergen St & Buffalo Ave           3
Lab - NYC                         2
Park Pl & Buffalo Ave             2
St Marks Ave & Ralph Ave          1
Name: start_station_name, dtype: int64

## 4. Create a new dataframe for the map 

#### a) Create a new list with just the value counts of the usage at each start station 

In [9]:
#Create a list to make a new dataframe of start stations with counts / usage

start_lst=citibike['start_station_name'].value_counts()

In [10]:
bike_freq = pd.DataFrame(start_lst)

In [11]:
bike_freq

start_station_name
Broadway & W 58 St                          11610
W 21 St & 6 Ave                             11219
West St & Chambers St                        8691
1 Ave & E 68 St                              8624
W 31 St & 7 Ave                              8610
...                                           ...
Sterling Pl & Schenectady Ave                   6
Bergen St & Buffalo Ave                         3
Lab - NYC                                       2
Park Pl & Buffalo Ave                           2
St Marks Ave & Ralph Ave                        1

[1661 rows x 1 columns]

#### b) Renaming of new dataframe 

In [12]:
#change the name of start_station_name to start_use_freq because the header has been shifted when converted to dataframe

bike_freq.rename(columns = {'start_station_name':'start_use_freq'}, inplace = True)

#### c) Shifting the index and columns for later mapping

In [13]:
#because the index is curently set with station names. The next step is to create a new column as start_station_name and reset the 0 column to a numeric index

#first step is to copy the index as station name

bike_freq['start_station_name'] = bike_freq.index

In [14]:
# Objective of this step is to turn the bike_freq dataframe with similar columns order so that we can map the bike usage frequency into the start_station dataframe which we will create later

# 1) We reset the first column as numeric index

bike_freq = bike_freq.reset_index(drop=True)

# 2) We reorder the sequence of the column for later feature engineering

bike_freq = bike_freq[['start_station_name', 'start_use_freq']]


In [15]:
bike_freq

start_station_name  start_use_freq
0                Broadway & W 58 St           11610
1                   W 21 St & 6 Ave           11219
2             West St & Chambers St            8691
3                   1 Ave & E 68 St            8624
4                   W 31 St & 7 Ave            8610
...                             ...             ...
1656  Sterling Pl & Schenectady Ave               6
1657        Bergen St & Buffalo Ave               3
1658                      Lab - NYC               2
1659          Park Pl & Buffalo Ave               2
1660       St Marks Ave & Ralph Ave               1

[1661 rows x 2 columns]

#### e) Create / setup a new dataframe with columns for the map

In [16]:
#We create a new dataframe with just the start station information.
# The column for station name, latitude and longitude is at col 4, 8 and 9

start_station_map = citibike.iloc[: , [4, 8, 9]].copy()

In [17]:
start_station_map

start_station_name  start_lat  start_lng
0                   2 Ave & E 29 St  40.741724 -73.978093
1             E 97 St & Madison Ave  40.787826 -73.953423
2             E 97 St & Madison Ave  40.787899 -73.953396
3        Morningside Ave & W 123 St  40.809931 -73.955209
4                   2 Ave & E 29 St  40.741803 -73.978004
...                             ...        ...        ...
2460100             E 75 St & 3 Ave  40.771129 -73.957723
2460101       Verona Pl & Fulton St  40.680356 -73.947679
2460102              30 Ave & 41 St  40.763422 -73.914142
2460103            Jay St & York St  40.701214 -73.986726
2460104      Harman St & Seneca Ave  40.705770 -73.912920

[2453885 rows x 3 columns]

In [18]:
# Note that we only need the unique value of each station as we are mapping the value count onto the above dataframe, we will drop the duplicate of this dataframe
# Duplicates is probably from the same station name but with slightly different start_lat / start_lng

start_station_map = start_station_map.drop_duplicates('start_station_name')

In [19]:
start_station_map

start_station_name  start_lat  start_lng
0                   2 Ave & E 29 St  40.741724 -73.978093
1             E 97 St & Madison Ave  40.787826 -73.953423
3        Morningside Ave & W 123 St  40.809931 -73.955209
5                     57 St & 4 Ave  40.642754 -74.016974
6                Avenue D & E 12 St  40.725806 -73.974225
...                             ...        ...        ...
2418485               41 St & 3 Ave  40.652405 -74.008758
2418598              30 Ave & 41 St  40.763296 -73.913985
2418643      Tiebout Ave & E 184 St  40.858498 -73.896370
2419960       Bailey Ave & W 193 St  40.870663 -73.906800
2424262                Picnic Point  40.685126 -74.025353

[1661 rows x 3 columns]

#### f) Turn bike_freq into dictionary to map 'start_use_freq' into the start_station_map

In [20]:
# the number of rows for start_station map and bike_freq matches. We are going to merge the 2 dataframe together

# 1) we convert the bike_freq into a dictionary

bike_freq_dict = dict(bike_freq.values)

# 2) we map this dictionary as a new column in start_station_map

start_station_map['start_use_freq'] = start_station_map['start_station_name'].map(bike_freq_dict)

#quick look at the new start_station_map

start_station_map

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == "__main__":


start_station_name  start_lat  start_lng  start_use_freq
0                   2 Ave & E 29 St  40.741724 -73.978093            5016
1             E 97 St & Madison Ave  40.787826 -73.953423            2562
3        Morningside Ave & W 123 St  40.809931 -73.955209            1093
5                     57 St & 4 Ave  40.642754 -74.016974             298
6                Avenue D & E 12 St  40.725806 -73.974225             882
...                             ...        ...        ...             ...
2418485               41 St & 3 Ave  40.652405 -74.008758             111
2418598              30 Ave & 41 St  40.763296 -73.913985             899
2418643      Tiebout Ave & E 184 St  40.858498 -73.896370             309
2419960       Bailey Ave & W 193 St  40.870663 -73.906800              26
2424262                Picnic Point  40.685126 -74.025353             237

[1661 rows x 4 columns]

#### g) Use a function to create a new column with usage category of V. High, High, Moderate, Mild, Low

In [21]:
# Now let's create a new column that categorise the usage frequency into Very High, High, Moderate, Low
# we will consider above 5000 as very high usage; 1000 - 5000 as High; below 1000 as moderate; below 200 as low

conditions = [
    (start_station_map['start_use_freq'] >= 5000),
    (start_station_map['start_use_freq'] >= 1000) & (start_station_map['start_use_freq'] < 5000),
    (start_station_map['start_use_freq'] >= 500) & (start_station_map['start_use_freq'] < 1000),
    (start_station_map['start_use_freq'] >= 100) & (start_station_map['start_use_freq'] < 500),
    (start_station_map['start_use_freq'] < 100)
]

values = ['V High', 'High', 'Moderate', 'Mild', 'Low']

start_station_map['usage_cat'] = np.select(conditions, values)

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [22]:
start_station_map

start_station_name  start_lat  start_lng  start_use_freq  \
0                   2 Ave & E 29 St  40.741724 -73.978093            5016   
1             E 97 St & Madison Ave  40.787826 -73.953423            2562   
3        Morningside Ave & W 123 St  40.809931 -73.955209            1093   
5                     57 St & 4 Ave  40.642754 -74.016974             298   
6                Avenue D & E 12 St  40.725806 -73.974225             882   
...                             ...        ...        ...             ...   
2418485               41 St & 3 Ave  40.652405 -74.008758             111   
2418598              30 Ave & 41 St  40.763296 -73.913985             899   
2418643      Tiebout Ave & E 184 St  40.858498 -73.896370             309   
2419960       Bailey Ave & W 193 St  40.870663 -73.906800              26   
2424262                Picnic Point  40.685126 -74.025353             237   

        usage_cat  
0          V High  
1            High  
3            High  
5            Mild  
6        Moderate  
...           ...  
2418485      Mild  
2418598  Moderate  
2418643      Mild  
2419960       Low  
2424262      Mild  

[1661 rows x 5 columns]

## 5. We are ready to creating a Geospatial Map to show the usage

We are going to use Folium to create a map with markers to show which stations has highest and lowest usage. It will also visually allow us to see which area / zone has high / low usage.

If you are interested to learn more about folim, the full documentation link is as follow:

https://python-visualization.github.io/folium/modules.html

In [23]:
#Let's see how our map may look like

start_use_map=folium.Map(
        location=[40.718502, -73.983299],
        zoom_start=12, 
        width = 900, height = 600, 
        control_scale=True)

for _, start_station in start_station_map.iterrows():
    folium.Marker(
        location=[start_station['start_lat'], start_station['start_lng']],
        popup=start_station['start_use_freq'],
        tooltip=start_station['start_station_name']
    ).add_to(start_use_map)

start_use_map

**Note** that the markers are all in default blue. As we need to differential which one has high and low usage, we need to add another column to change the marker colours.

Also when u hover over the marker you will see the 'start_station_name'. Click on it you will see the total no of usage for the station in November.

#### Use a function to color code the usage_cat

The color options for folium is as follows:
color_options = {'beige', 'black', 'blue', 'cadetblue', 'darkblue', 'darkgreen', 'darkpurple', 'darkred', 'gray', 'green', 'lightblue', 'lightgray', 'lightgreen', 'lightred', 'orange', 'pink', 'purple', 'red', 'white'}

In [24]:
#creating a function to define the markers to specific color

def select_marker_color(row):
    if row['usage_cat'] == 'V High':
        return 'red'
    elif row['usage_cat'] == 'High':
        return 'orange'
    elif row['usage_cat'] == 'Moderate':
        return 'beige'
    elif row['usage_cat'] == 'Mild':
        return 'gray'
    elif row['usage_cat'] == 'Low':
        return 'lightgray'

#### Apply color function onto the start_station_map as a new column call color

In [25]:
#add in a new 'color' column into start_station_map

start_station_map['color'] = start_station_map.apply(select_marker_color, axis=1)
start_station_map

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


start_station_name  start_lat  start_lng  start_use_freq  \
0                   2 Ave & E 29 St  40.741724 -73.978093            5016   
1             E 97 St & Madison Ave  40.787826 -73.953423            2562   
3        Morningside Ave & W 123 St  40.809931 -73.955209            1093   
5                     57 St & 4 Ave  40.642754 -74.016974             298   
6                Avenue D & E 12 St  40.725806 -73.974225             882   
...                             ...        ...        ...             ...   
2418485               41 St & 3 Ave  40.652405 -74.008758             111   
2418598              30 Ave & 41 St  40.763296 -73.913985             899   
2418643      Tiebout Ave & E 184 St  40.858498 -73.896370             309   
2419960       Bailey Ave & W 193 St  40.870663 -73.906800              26   
2424262                Picnic Point  40.685126 -74.025353             237   

        usage_cat      color  
0          V High        red  
1            High     orange  
3            High     orange  
5            Mild       gray  
6        Moderate      beige  
...           ...        ...  
2418485      Mild       gray  
2418598  Moderate      beige  
2418643      Mild       gray  
2419960       Low  lightgray  
2424262      Mild       gray  

[1661 rows x 6 columns]

In [26]:
#Let's add in a new color line in our Folium Map

start_use_map=folium.Map(
        location=[40.718502, -73.983299],
        zoom_start=12, 
        width = 900, height = 1200, 
        control_scale=True)

for _, start_station in start_station_map.iterrows():
    folium.Marker(
        location=[start_station['start_lat'], start_station['start_lng']],
        popup=start_station['start_use_freq'],
        tooltip=start_station['start_station_name'],
        icon=folium.Icon(color=start_station['color'])
    ).add_to(start_use_map)

start_use_map